<center><h1>YOLO11 Training</h1>
<h2>Matthias Bartolo</h2>

</center>

<h3>Package Imports</h3>

In [1]:
# !pip install --upgrade roboflow ultralytics

**<h3>Required libraries.</h3>**

In [2]:
import torch
import os
import ultralytics
import locale
import glob
import pandas as pd
import matplotlib.pyplot as plt

from IPython import display
from ultralytics import YOLO
from IPython.display import display, Image
from roboflow import Roboflow

%matplotlib inline

**<h3>Using GPU if one is available.</h3>**

In [ ]:
!nvidia-smi

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(device)

In [ ]:
# Retrieving the current working directory
HOME = os.getcwd()
print(HOME)

**<h3>Downloading the Roboflow dataset.</h3>**

In [ ]:
if not os.path.isdir(os.path.join(HOME, 'datasets')):
    os.mkdir(os.path.join(HOME, 'datasets'))
os.chdir(os.path.join(HOME, 'datasets'))


rf = Roboflow(api_key="<ROBOFLOW API KEY>")
project = rf.workspace("<WORKSPACE>").project("<PROJECT>")
version = project.version(2)
dataset = version.download("yolov11")

**<h3>Training the YOLO11 model.</h3>**

In [ ]:
# Specifying the paths
model_path = 'yolo11m.pt'

yaml_path  = dataset.location+"/data.yaml"

# Creating YOLO object
model = YOLO(model_path)

# Specifying training parameters
num_epochs = 100  # Number of epochs
batch_size = 16 #8 # Adjust based on GPU memory
image_size = 640  # Decrease for faster training

# Training configuration
train_config = {
    'data': yaml_path,
    'imgsz': image_size,
    'batch': batch_size,
    'epochs': num_epochs,
    'device': 0,  # Use GPU 0
    # 'workers': 1,  # Number of data loading workers
    'optimizer': 'Adam',  # Use Adam optimizer
    'cache': True,#'disk',  # Cache images for faster training
    'patience': 10,  # epochs to wait before decreasing LR
    'val': True,  # Run validation during training
    'plots': True,  # Run plots during training
}

# Train the model
model.train(**train_config)


**<h3>Validating the YOLO11 model on the Validation subset.</h3>**

In [8]:
locale.getpreferredencoding = lambda: "UTF-8"
# !pip install aspose-words

In [ ]:
model.val() #This will output a train file however it will be on the validation data

**<h3>Validating the YOLO11 model on the Testing subset.</h3>**

In [ ]:
model.val(split='test') #This will output a train file however it will be on the test data

**<h3>Testing the YOLO11 model on the Testing subset.</h3>**

In [ ]:
!yolo task=detect \
mode=predict \
model={HOME}/datasets/runs/detect/train1/weights/best.pt \
source={dataset.location}/test/images \
save=True

**<h3>Training Results.</h3>**

In [ ]:
from IPython.display import Image as IPyImage

IPyImage(filename=f'{HOME}/datasets/runs/detect/train/results.png', width=600)

**<h3>Testing Resultant Images.</h3>**

In [ ]:
counter =0
limit = 10
for image_path in glob.glob(f'{HOME}/datasets/runs/detect/predict/*.jpg'):
      display(Image(filename=image_path))
      print("\n")
      counter += 1
      if counter == limit:
          break